# Setting up the environment

In [1]:
!pip install pymupdf --quiet

In [2]:
import re
import warnings

import fitz
import nltk
import torch
from nltk.tokenize import sent_tokenize
from peft import AutoPeftModelForSeq2SeqLM
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer, logging

CKPT_PATH = "facebook/bart-large-cnn" # Path to the fine-tuned base model
HF_REPO_PATH = "spolivin/bart-arxiv-lora" # Path to the repo where LoRA adapters are saved

warnings.filterwarnings("ignore")
logging.set_verbosity_error()
nltk.download("punkt_tab")
nltk.download("punkt")

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

# Loading models to be tested

In [3]:
tokenizer = AutoTokenizer.from_pretrained(CKPT_PATH)
original_model = AutoModelForSeq2SeqLM.from_pretrained(CKPT_PATH)

lora_model = AutoPeftModelForSeq2SeqLM.from_pretrained(HF_REPO_PATH)

# Defining functions for retrieving/preprocessing text from PDF

In [4]:
def prettify_summary(summary):
    """Prettifies the summary."""
    # Spliting input into sentences and capitalizing each one
    sentences = sent_tokenize(summary)
    prettified_summary = " ".join(s.capitalize() for s in sentences)

    # Removing unwanted spaces before punctuation
    prettified_summary = re.sub(r'\s+([.,!?])', r'\1', prettified_summary)

    return prettified_summary

In [5]:
def summarize_text(
    model,
    tokenizer,
    text,
    device="cuda",
    max_input_length=1024,
    max_output_length=250,
):
    """Tokenizes and generates a summary based on input text."""
    inputs = tokenizer(
        text,
        return_tensors="pt",
        truncation=True,
        max_length=max_input_length
    ).to(device)

    summary_ids = model.generate(
      **inputs,
      max_length=max_output_length,
      num_beams=4,
      early_stopping=True
    )

    # Decoding and prettifying output
    raw_summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)

    return prettify_summary(raw_summary)

In [6]:
def extract_main_text(pdf_path: str, beginning="introduction") -> str:
    """Retrieves the article text after abstract and before references.

       Args:
            pdf_path (str): Path to the pdf-file with the article.
            beginning (str, optional): The beginning from which to start retrieving text.
                                      Defaults to "introduction".
       Returns:
            str: Extracted text.
    """
    # Extracting text from each page
    doc = fitz.open(pdf_path)
    full_text = ""
    for page in doc:
        full_text += page.get_text("text") + "\n"

    # Finding the start of the main text (after Abstract)
    abstract_end_idx = full_text.lower().find(beginning) + len(beginning)
    if abstract_end_idx == -1:  # If "Introduction" not found, falling back to first line after "Abstract"
        abstract_end_idx = full_text.lower().find("abstract") + len("abstract")

    # Finding the end of the main text (before References)
    references_idx = full_text.lower().find("references")
    if references_idx == -1:  # If "References" section not found, extracting till the end
        references_idx = len(full_text)

    # Extract only the part between Abstract and References
    main_text = full_text[abstract_end_idx:references_idx].strip()
    return main_text

In [7]:
def clean_text(text):
    """Cleans the extracted paper text."""
    text = re.sub(r'\s+', ' ', text)

    return text.strip()

# Generating summaries on sample articles

**NOTE:** *In order to test the summarization models one needs to firstly download the articles in pdf and upload to Google Colab*:

* [Efficient Estimation of Word Representations in Vector Space](https://arxiv.org/abs/1301.3781)
* [Attention Is All You Need](https://arxiv.org/abs/1706.03762)
* [Recurrent Neural Networks (RNNs): A gentle Introduction and Overview](https://arxiv.org/abs/1912.05911)

## Article 1: [Efficient Estimation of Word Representations in Vector Space](https://arxiv.org/abs/1301.3781)

### Retrieving article text

In [8]:
article_pdf_path_1 = "/content/1301.3781v3.pdf"

In [9]:
# Example usage
article_text = extract_main_text(pdf_path=article_pdf_path_1, beginning="introduction")
article_text_cleaned = clean_text(article_text)
article_text_cleaned[:1000]

'Many current NLP systems and techniques treat words as atomic units - there is no notion of similar- ity between words, as these are represented as indices in a vocabulary. This choice has several good reasons - simplicity, robustness and the observation that simple models trained on huge amounts of data outperform complex systems trained on less data. An example is the popular N-gram model used for statistical language modeling - today, it is possible to train N-grams on virtually all available data (trillions of words [3]). However, the simple techniques are at their limits in many tasks. For example, the amount of relevant in-domain data for automatic speech recognition is limited - the performance is usually dominated by the size of high quality transcribed speech data (often just millions of words). In machine translation, the existing corpora for many languages contain only a few billions of words or less. Thus, there are situations where simple scaling up of the basic technique

### Generating summaries

In [10]:
lora_summary = summarize_text(model=lora_model.to("cuda"), tokenizer=tokenizer, text=article_text_cleaned)
lora_summary

'We develop new techniques for learning high-quality word vectors from huge data sets with billions of words, and with millions of words in the vocabulary. We use recently proposed techniques for measuring the quality of the resulting vector representa- tions, with the expectation that not only will similar words tend to be close to each other, but that words can have multiple degrees of similarity. We design a new comprehensive test set for measuring both syntactic and semantic regularities1, and show that many such regularities can be learned with high accuracy. We discuss how training time and accuracy depends on the dimensionality of the word vectors and on the amount of the training data.'

In [11]:
original_summary = summarize_text(model=original_model.to("cuda"), tokenizer=tokenizer, text=article_text_cleaned)
original_summary

'Many current nlp systems and techniques treat words as atomic units - there is no notion of similar- ity between words. This choice has several good reasons - simplicity, robustness and the observation that simple models trained on huge amounts of data outperform complex systems trained on less data. The main goal of this paper is to introduce techniques that can be used for learning high-quality word vectors from huge data sets with billions of words.'

## Article 2: [Attention Is All You Need](https://arxiv.org/abs/1706.03762)

In [12]:
article_pdf_path_2 = "/content/1706.03762v7.pdf"

In [13]:
# Example usage
article_text = extract_main_text(article_pdf_path_2)
article_text_cleaned = clean_text(article_text)
article_text_cleaned[:1000]

'Recurrent neural networks, long short-term memory [13] and gated recurrent [7] neural networks in particular, have been firmly established as state of the art approaches in sequence modeling and transduction problems such as language modeling and machine translation [35, 2, 5]. Numerous efforts have since continued to push the boundaries of recurrent language models and encoder-decoder architectures [38, 24, 15]. Recurrent models typically factor computation along the symbol positions of the input and output sequences. Aligning the positions to steps in computation time, they generate a sequence of hidden states ht, as a function of the previous hidden state ht−1 and the input for position t. This inherently sequential nature precludes parallelization within training examples, which becomes critical at longer sequence lengths, as memory constraints limit batching across examples. Recent work has achieved significant improvements in computational efficiency through factorization tricks

In [14]:
lora_summary = summarize_text(model=lora_model.to("cuda"), tokenizer=tokenizer, text=article_text_cleaned)
lora_summary

'The transformer is the first transduction model relying entirely on self-attention to compute representations of its input and output without using sequence- aligned rnns or convolutional neural networks as basic building block, computing hidden representations in parallel for all input andoutput positions. The transformer allows for significantly more parallelization and can reach a new state of the art in translation quality after being trained for as little as twelve hours on eight p100 gpus. In the following sections, we describe the model architecture, motivate selfattention and discuss its advantages over models such as [17, 18] and convs2s [9].'

In [15]:
original_summary = summarize_text(model=original_model.to("cuda"), tokenizer=tokenizer, text=article_text_cleaned)
original_summary

'Recurrent neural networks, long short-term memory [13] and gated recurrent [7] neural networks have been firmly established as state of the art approaches in sequence modeling and transduction problems. In this work we propose the transformer, a model architecture eschewing recurrence and relying entirely on an attention mechanism to draw global dependencies between input and output. The transformer allows for significantly more parallelization and can reach a new state-of-the-art in translation quality after being trained for as little as twelve hours on eight p100 gpus.'

## Article 3: [Recurrent Neural Networks (RNNs): A gentle Introduction and Overview](https://arxiv.org/abs/1912.05911)

In [16]:
article_pdf_path_3 = "/content/1912.05911v1.pdf"

In [17]:
# Example usage
article_text = extract_main_text(pdf_path=article_pdf_path_3, beginning="introduction & notation")
article_text_cleaned = clean_text(article_text)
article_text_cleaned[:1000]

'Recurrent Neural Networks (RNNs) are a type of neural network architecture which is mainly used to detect patterns in a sequence of data. Such data can be handwriting, genomes, text or numerical time series which are often produced in industry settings (e.g. stock markets or sensors) [7, 12]. However, they are also applicable to images if these get respectively decomposed into a series of patches and treated as a sequence [12]. On a higher level, RNNs ﬁnd applications in Language Modelling & Generating Text, Speech Recognition, Generating Image Descriptions or Video Tagging. What differentiates Recurrent Neural Networks from Feedforward Neural Networks also known as Multi-Layer Perceptrons (MLPs) is how information gets passed through the network. While Feedforward Networks pass information through the network without cycles, the RNN has cycles and transmits information back into itself. This enables them to extend the functionality of Feedforward Networks to also take into account pr

In [18]:
lora_summary = summarize_text(model=lora_model.to("cuda"), tokenizer=tokenizer, text=article_text_cleaned)
lora_summary

'Recurrent neural networks (rnns) are a type of neural network architecture which is mainly used to detect patterns in a sequence of data such as handwriting, genomes, text or numerical time series. While feedforward networks pass information through the network without cycles, the rnn has cycles and transmits information back into itself. This enables them to extend the functionality of feedforward neural networks to also take into account previous inputs x0:t−1 and not only the current input xt. In this paper, we show how to construct a recurrent neural network using the backpropagation through time (bptt) and truncated bptt algorithm for rnns.'

In [19]:
original_summary = summarize_text(model=original_model.to("cuda"), tokenizer=tokenizer, text=article_text_cleaned)
original_summary

'Recurrent neural networks (rnns) are a type of neural network architecture. They are mainly used to detect patterns in a sequence of data. Rnns have applications in language modelling & generating text, speech recognition, generating image descriptions or video tagging. Backpropagation through time (bptt) is used to backpropagate the error through a rnn.'